In [1]:
import os
#os.environ["CUDA_VISIBLE_DEVICES"] = "1"
#os.environ["CUDA_LAUNCH_BLOCKING"]= "1"

#no dis

from BART_LOSS_53 import *
import torch.utils.data as Data
import torch.optim as optim
from torch.autograd import Variable
from mlp_mixer_pytorch_12 import MLPMixer as MLPMixer
from mlp_mixer_pytorch_12 import weight_init
import torch
import pandas as pd
from torchsummary import summary

from torch.optim import lr_scheduler
from torch.optim.lr_scheduler import ReduceLROnPlateau
from torch.optim.lr_scheduler import CosineAnnealingLR
from torch.optim.lr_scheduler import StepLR
from torch.optim.lr_scheduler import ExponentialLR

In [2]:
target_size = 48
batch_size = 3

epochs = 1000000

#epochs = 1

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

myNet = MLPMixer(in_channels=1, dim=48, num_classes=48*48, image_size=48, depth=1, token_dim=48,
                     channel_dim=48).to(device)

#myNet.apply(weight_init)

myNet.to(device)
#summary(myNet,(1,48,48))

MLPMixer(
  (to_input_arrange): Sequential(
    (0): Reduce('b c h w -> b h w', 'mean')
    (1): Rearrange('b h w -> b h w')
  )
  (mixer_blocks): ModuleList(
    (0): MixerBlock(
      (row_mixer): Sequential(
        (0): LayerNorm((48,), eps=1e-05, elementwise_affine=True)
        (1): Rearrange('b h w -> b w h')
        (2): FeedForward(
          (net): Sequential(
            (0): Linear(in_features=48, out_features=48, bias=True)
            (1): GELU()
            (2): Dropout(p=0.0, inplace=False)
            (3): Linear(in_features=48, out_features=48, bias=True)
            (4): Dropout(p=0.0, inplace=False)
          )
        )
        (3): Rearrange('b w h -> b h w')
      )
      (column_mixer): Sequential(
        (0): LayerNorm((48,), eps=1e-05, elementwise_affine=True)
        (1): FeedForward(
          (net): Sequential(
            (0): Linear(in_features=48, out_features=48, bias=True)
            (1): GELU()
            (2): Dropout(p=0.0, inplace=False)
        

In [3]:
def save_result(allOutPut,all_files, save_dir = './BART/result_2020_8_5'):
    if not os.path.exists(save_dir):
        os.makedirs(save_dir)
    allOutPut = allOutPut.reshape(-1,1,target_size, target_size)
    for index, each_day in tqdm(enumerate(allOutPut)):
        for index_one, each in enumerate(allOutPut[index]):
            
            each = np.round(each)
            data = pd.DataFrame(data=each)
            data.to_csv(f'{save_dir}/{all_files[index]}')
        
    print('Finished predict')

In [4]:
train_data, label_data, all_files = load_data_for_more_loss(predict=True)

# 构建数据
trainData = train_data
#trainData = train_data.permute(0,2,3,1)
labelData = label_data.clone()
#labelData = label_data.clone().permute(0,2,3,1)

#print(trainData.shape)
#print(labelData.shape)

train_data = Data.TensorDataset(trainData, labelData)


# 构建训练集
train_loader = Data.DataLoader(
    dataset=train_data,
    batch_size=batch_size,
    shuffle=True,
    num_workers=0
)


['2020-8-10.csv', '2020-8-11.csv', '2020-8-12.csv', '2020-8-13.csv', '2020-8-14.csv', '2020-8-17.csv', '2020-8-18.csv', '2020-8-19.csv', '2020-8-20.csv', '2020-8-21.csv', '2020-8-24.csv', '2020-8-25.csv', '2020-8-26.csv', '2020-8-27.csv', '2020-8-28.csv', '2020-8-3.csv', '2020-8-4.csv', '2020-8-5.csv', '2020-8-6.csv', '2020-8-7.csv']


In [5]:
#params = [p for p in myNet.parameters() if p.requires_grad]
#optimizer = optim.SGD(params, lr=0.0001, momentum=0.9, weight_decay=1E-4)
#optimizer = optim.SGD(myNet.parameters(), lr=0.1)
optimizer = torch.optim.Adam(myNet.parameters(), lr=10)
#lr_scheduler = ExponentialLR(optimizer, gamma=0.9996)
#lr_scheduler = CosineAnnealingLR(optimizer, T_max=32, eta_min=0, verbose=True)
lr_scheduler = ReduceLROnPlateau(optimizer, mode='min', factor=0.8, patience=300, verbose=True, threshold=0.0001, threshold_mode='rel', cooldown=0, min_lr=0, eps=1e-8)

earlyStop = 5000
earlyStep = 0
best_loss = float('inf')
needSave = False
save_path = r'C:/Users/remote/Desktop/lan-resnet-fina/BART/result_2020_8_5/makabaka.pth'  # 模型存储的地址和名字


In [6]:
start_epoch = 0
RESUME =  False     # 设置是否需要从上次的状态继续训练
if RESUME:
    path_checkpoint = r'C:/Users/remote/Desktop/lan-resnet-fina/BART/result_2020_8_5/models/checkpoint/ckpt_best.pth'  # 断点路径
    checkpoint = torch.load(path_checkpoint, map_location=torch.device('cpu'))  # 加载断点

    myNet.load_state_dict(checkpoint['net'])  # 加载模型可学习参数

    optimizer.load_state_dict(checkpoint['optimizer'])  # 加载优化器参数
    start_epoch = checkpoint['epoch'] +1  # 设置开始的epoch
    
    #lr_scheduler.load_state_dict(checkpoint['lr_scheduler'])


In [7]:
max_norm = None
for epoch in range(start_epoch, epochs):
    # ---------------------------
    # train model
    myNet.train()

    earlyStep += 1
    running_loss = 0.0
    
    train_bar = tqdm(train_loader)
    allOutPut = None
    for step, data in enumerate(train_bar):
        
        images, labels = data
        #image = Variable(images, requires_grad = True)
        #labels = Variable(labels, requires_grad = True)
        images.to(device)
        labels.to(device)
        #print('images:', images)
        #print('images.shape:', images.shape)
        #print('labels:', labels)
        #print('labels.shape:', labels.shape)
        
        logits = myNet(images.to(device))
        #print('logits:', logits)
        #print('logits.shape:', logits.shape)
        #print('labels.shape:', labels.shape)

        loss = computelossforSix(logits, labels.to(device), device=device, targetShape=target_size)
        #loss = computeloss(logits.to(device), labels.to(device), device=device, targetShape=target_size)
        #loss = computelossforSimilarOnSpace(logits[0], labels[0].to(device), device=device, targetShape=target_size)
        #loss = computelossforSymmetric(logits[0], labels[0].to(device), device=device, targetShape=target_size)
        #print('LOSS:', loss)
        
        '''
        # Compute L1 loss component
        l1_weight = 0.00000001
        l1_norm = sum(parameters.abs().sum()
                  for parameters in myNet.parameters())
        #print('L1:',l1_weight * l1_norm)
        #print('LOSS:', loss)
        loss = loss + l1_weight * l1_norm
        '''

        optimizer.zero_grad() #梯度置0
   
        loss.backward()
        
        if max_norm:
            nn.utils.clip_grad_norm(myNet.parameters(), max_norm=1)
        
        optimizer.step()


        # print statistics
        running_loss += loss.item()
        #print('running_loss', running_loss)
        

        train_bar.desc = "train epoch[{}/{}] loss:{:.3f}".format(epoch + 1,
                                                                 epochs,
                                                                 loss)
        save_data = logits.cpu().detach().numpy()

        if step == 0:
            allOutPut = save_data
            
        else:
            allOutPut = np.vstack((allOutPut, save_data))

    # ----------------------------
    # 设置早停
    now_loss = running_loss/len(train_loader)
    #print('running_loss', running_loss)
    #lr_scheduler.step()
    lr_scheduler.step(now_loss)
    #print('now_loss', now_loss)

    if now_loss < best_loss:
        earlyStep = 0
        best_loss = now_loss

        checkpoint = {
            "net": myNet.state_dict(),
            'optimizer':optimizer.state_dict(),
            "epoch": epoch,
            'lr_scheduler': lr_scheduler.state_dict()
        }
        if not os.path.isdir("C:/Users/remote/Desktop/lan-resnet-fina/BART/result_2020_8_5/models/checkpoint"):
          os.makedirs("C:/Users/remote/Desktop/lan-resnet-fina/BART/result_2020_8_5/models/checkpoint")
        #torch.save(checkpoint, "C:/Users/remote/Desktop/lan-resnet-fina/BART/result_test5/models/checkpoint/ckpt_best_%s.pth" %(str(epoch)))
        torch.save(checkpoint, "C:/Users/remote/Desktop/lan-resnet-fina/BART/result_2020_8_5/models/checkpoint/ckpt_best.pth")

        if needSave:
            torch.save(myNet.state_dict(), save_path)
        print(f"save files with loss {best_loss}")
        #allOutPut = allOutPut.transpose(1, 0, 2)
        #print('allOutPut:',allOutPut)
        #allOutPut = allOutPut * max_num.detach().cpu().numpy()
        save_result(allOutPut, all_files)

    if earlyStep > earlyStop:
        print(f"{earlyStep} 次没有最好的loss了！")
        break

print('Finished Training')


train epoch[1/1000000] loss:2117.938: 100%|██████████| 7/7 [00:02<00:00,  3.14it/s]


save files with loss 2453.8799176897323


20it [00:00, 400.00it/s]


Finished predict


train epoch[2/1000000] loss:2166.509: 100%|██████████| 7/7 [00:00<00:00, 23.81it/s]


...

train epoch[44915/1000000] loss:17.001: 100%|██████████| 7/7 [00:00<00:00, 39.99it/s]


train epoch[45105/1000000] loss:18.478: 100%|██████████| 7/7 [00:00<00:00, 40.46it/s]


train epoch[45295/1000000] loss:13.981: 100%|██████████| 7/7 [00:00<00:00, 41.41it/s]


train epoch[45485/1000000] loss:26.302: 100%|██████████| 7/7 [00:00<00:00, 40.22it/s]

5001 次没有最好的loss了！
Finished Training
